In [ ]:
%pip install faiss-cpu


Note: you may need to restart the kernel using dbutils.library.restartPython() to use updated packages.
Note: you may need to restart the kernel using dbutils.library.restartPython() to use updated packages.


In [ ]:
dbutils.library.restartPython()

In [ ]:
from pyspark.sql import SparkSession

# Initialize Spark session
park = SparkSession.builder.appName("reading-parquet-file").getOrCreate()

# Read parquet file as DataFrame
df = spark.read.parquet("/mnt/adlsdl/raw/open-australian-legal-corpus/")

# Show the contents of the DataFrame
df.count()

display(df)

version_id type jurisdiction source citation url text federal_court_of_australia:fca/single/2019/2019fca0778 decision commonwealth federal_court_of_australia AXL17 v Minister for Immigration and Border Protection (No 2) [2019] FCA 778 https://www.judgments.fedcourt.gov.au/judgments/Judgments/fca/single/2019/2019fca0778 FEDERAL COURT OF AUSTRALIA

AXL17 v Minister for Immigration and Border Protection (No 2) [2019] FCA 778
Appeal from: AXL17 v Minister for Immigration [2018] FCCA 2077

File number: NSD 1459 of 2018

Judge: MARKOVIC J

Date of judgment: 30 May 2019

Catchwords: MIGRATION – appeal from orders of the Federal Circuit Court of Australia (Federal Circuit Court) dismissing the appellants’ application for judicial review – where the Administrative Appeals Tribunal (Tribunal) affirmed the decision of a delegate not to grant the appellants protection visas – whether to grant leave to the appellants to rely on grounds of appeal not raised before the Federal Circuit Court – whether the Tribunal asked the first appellant to change his political views – whether the Tribunal failed to consider the practicalities of relocating for the appellants – whether the Tribunal was required to consider what was in the best interests of the children – whether the Tribunal assumed or found that the appellants would have family support – whether the Tribunal failed to consider threats to the third and fourth appellants – appeal dismissed

Legislation: Migration Act 1958 (Cth) s 36

Cases cited: Appellant S395/2002 v Minister for Immigration and Multicultural Affairs (2003) 216 CLR 473
 DHK16 v Minister for Immigration and Border Protection [2018] FCA 1353
 Minister for Immigration and Ethnic Affairs v Teoh (1995) 183 CLR 273
 SZLPH v Minister for Immigration and Border Protection [2018] FCAFC 145
 Wan v Minister of Immigration and Multicultural Affairs (2001) 107 FCR 133
 YNQY v Minister for Immigration and Border Protection [2017] FCA 1466

Date of hearing: 28 February 2019

Date of last submissions: 13 March 2019 (Respondent)
 21 March 2019 (Applicant)

Registry: New South Wales

Division: General Division

National Practice Area: Administrative and Constitutional Law and Human Rights

Category: Catchwords

Number of paragraphs: 68

Counsel for the Appellants: The First and Second Appellants appeared in person on behalf of all the Appellants

Solicitor for the First Respondent: Mr S Valliappan of DLA Piper Australia

Counsel for the Second Respondent: The Second Respondent filed a submitting notice save as to costs


ORDERS
 NSD 1459 of 2018

BETWEEN: AXL17
 First Appellant

 AXM17
 Second Appellant

 AXN17 (and another named in the Schedule) by their litigation representative AXL17 (the First Appellant)
 Third Appellant

AND: MINISTER FOR IMMIGRATION AND BORDER PROTECTION
 First Respondent

 ADMINISTRATIVE APPEALS TRIBUNAL
 Second Respondent



JUDGE: MARKOVIC J
DATE OF ORDER: 30 May 2019


THE COURT ORDERS THAT:

1. The appeal be dismissed.
2. The first and second appellants pay the first respondent’s costs as agreed or taxed.
Note: Entry of orders is dealt with in Rule 39.32 of the Federal Court Rules 2011.

REASONS FOR JUDGMENT

MARKOVIC J:
1 This is an appeal from orders made by the Federal Circuit Court of Australia (Federal Circuit Court) on 31 July 2018 dismissing an application for judicial review of a decision of the second respondent (Tribunal): AXL17 v Minister for Immigration [2018] FCCA 2077 (AXL17). The Tribunal had affirmed a decision of a delegate of the first respondent, the Minister for Immigration and Border Protection (Minister), refusing to grant the appellants a protection visa.

background
2 The appellants are citizens of Sri Lanka who arrived in Australia on 11 April 2014 as the holders of visitor visas. The first appellant is the husband (Husband), the second appellant is his wife (Wife) and the third and fourth appellants are their children (collectively Children). On 22 February 2019 the Court made orders appo

In [ ]:
from pyspark.sql import SparkSession

df.createTempView("australian_legal_corpus")


In [ ]:
%sql

WITH IntellectualRows AS (
  SELECT *
  FROM australian_legal_corpus
  WHERE CONCAT(jurisdiction, ' ', source, ' ', citation, ' ', url, ' ', text) ILIKE '%Intellectual Property%'
)

SELECT COUNT(*) AS total_number_of_rows
FROM IntellectualRows;

total_number_of_rows 2991

In [ ]:
from pyspark.sql import SparkSession

spark = SparkSession.builder.appName("Embeddings").getOrCreate()

sql_query= """SELECT text
  FROM australian_legal_corpus
  WHERE CONCAT(jurisdiction, ' ', source, ' ', citation, ' ', url, ' ', text) ILIKE '%Intellectual Property%'"""

df = spark.sql(sql_query)
df.show(truncate=False)

In [ ]:
pandas_df = df.toPandas()
text_list = list(pandas_df['text'])
print(text_list[0:10])

['FEDERAL COURT OF AUSTRALIA\n\nMonroe Topple & Associates Pty Ltd v Institute of Chartered Accountants in Australia [2002] FCAFC 197\nTRADE PRACTICES – restrictive trade practices – misuse of market power – exclusive dealing – arrangements restricting dealings or affecting competition – appellant in business of providing course materials and other training support to candidates undertaking studies for their “Professional Year” (PY) in order to qualify to apply to become members of respondent and to practise as Chartered Accountants – respondent a non-profit organisation incorporated by Royal Charter – respondent in competition with CPA Australia and other bodies in providing certification of accountants (“certification market”) – respondent the only body which can authorise use of designation Chartered Accountant or acronym “CA” – respondent also selling support materials in competition with appellant and other entities (“PY support market”) – in return for enrolment fee in PY subject

In [ ]:
from langchain.embeddings.openai import OpenAIEmbeddings
from langchain.vectorstores import FAISS
from langchain.text_splitter import CharacterTextSplitter
from langchain.text_splitter import RecursiveCharacterTextSplitter
from langchain.text_splitter import TokenTextSplitter

text_content = '\n'.join(text_list)
text_splitter = TokenTextSplitter(chunk_size=1100, chunk_overlap=300)
chunks = text_splitter.split_text(text_content)

# text_splitter = RecursiveCharacterTextSplitter(chunk_size=300, chunk_overlap=50)
# text_splitter = RecursiveCharacterTextSplitter.from_tiktoken_encoder(chunk_size=300, chunk_overlap=50)
# text_splitter = CharacterTextSplitter(separator='\n', chunk_size=500, chunk_overlap=100)

In [ ]:
import os
import pickle
from time import sleep
from langchain.embeddings.openai import OpenAIEmbeddings
from langchain.vectorstores import FAISS
os.environ["OPENAI_API_KEY"] =""
total_length = len(chunks)
batch_size = 1000

db_directory = "/dbfs/mnt/adlsdl/raw/new_directory/"

for batch_start in range(0, total_length, batch_size):
    batch_end = min(batch_start + batch_size, total_length)
    batch_chunks = chunks[batch_start:batch_end]

    embeddings = OpenAIEmbeddings()
    db =FAISS.from_texts(texts=batch_chunks, embedding=embeddings)

    dbfs_file_path = f"{db_directory}vectorstore_batch_{batch_start}_{batch_end}.faiss"

    with open(dbfs_file_path, 'wb') as file:
        pickle.dump(db, file)
        print(f"Embeddings for batch {batch_start}-{batch_end} saved to {dbfs_file_path}")
    sleep(40)



In [ ]:
import os
from langchain.vectorstores import FAISS
from langchain.embeddings.openai import OpenAIEmbeddings
import pickle

db_directory = "/dbfs/mnt/adlsdl/raw/new_directory/vectorstore_batch_0_1000.faiss"
with open(db_directory, 'rb') as file:
    vectorstore=pickle.load(file)
    print("loaded")


loaded


### Demo

In [ ]:
query = "What is the background and context of the legal case involving Monroe Topple & Associates Pty Ltd and the Institute of Chartered Accountants in Australia?"
query1 = "How does the appellant, Monroe Topple & Associates Pty Ltd, engage in business, and what services does it provide?"
docs = vectorstore.similarity_search_with_score(query)
print(docs)

[(Document(page_content='FEDERAL COURT OF AUSTRALIA\n\nMonroe Topple & Associates Pty Ltd v Institute of Chartered Accountants in Australia [2002] FCAFC 197\nTRADE PRACTICES – restrictive trade practices – misuse of market power – exclusive dealing – arrangements restricting dealings or affecting competition – appellant in business of providing course materials and other training support to candidates undertaking studies for their “Professional Year” (PY) in order to qualify to apply to become members of respondent and to practise as Chartered Accountants – respondent a non-profit organisation incorporated by Royal Charter – respondent in competition with CPA Australia and other bodies in providing certification of accountants (“certification market”) – respondent the only body which can authorise use of designation Chartered Accountant or acronym “CA” – respondent also selling support materials in competition with appellant and other entities (“PY support market”) – in return for enro

In [ ]:
db_directory = "/dbfs/mnt/adlsdl/raw/new_directory/"
final_vectorstore = "/dbfs/mnt/adlsdl/raw/new_directory/vectorstore_batch_0_1000.faiss"
file_list = os.listdir(db_directory)
combine_vectorstore = "/dbfs/mnt/adlsdl/raw/new_directory/combine_vectorstore.faiss"

with open(final_vectorstore, 'rb') as file:
    vectorstore1=pickle.load(file)

for file_name in file_list:
    if file_name != "vectorstore_batch_0_1000.faiss":
        file_directory = os.path.join(db_directory, file_name)
        print(file_directory)
        with open(file_directory, 'rb') as file1:
            vectorstore2 = pickle.load(file1)
        vectorstore1.merge_from(vectorstore2)

with open(combine_vectorstore, 'wb') as file2:
    pickle.dump(vectorstore1, file2)

# print(type(vectorstore1))
# print(vectorstore1.docstore._dict)

/dbfs/mnt/adlsdl/raw/new_directory/vectorstore_batch_100000_101000.faiss
/dbfs/mnt/adlsdl/raw/new_directory/vectorstore_batch_10000_11000.faiss
/dbfs/mnt/adlsdl/raw/new_directory/vectorstore_batch_1000_2000.faiss
/dbfs/mnt/adlsdl/raw/new_directory/vectorstore_batch_101000_102000.faiss
/dbfs/mnt/adlsdl/raw/new_directory/vectorstore_batch_102000_103000.faiss
/dbfs/mnt/adlsdl/raw/new_directory/vectorstore_batch_103000_104000.faiss
/dbfs/mnt/adlsdl/raw/new_directory/vectorstore_batch_104000_105000.faiss
/dbfs/mnt/adlsdl/raw/new_directory/vectorstore_batch_105000_106000.faiss
/dbfs/mnt/adlsdl/raw/new_directory/vectorstore_batch_106000_107000.faiss
/dbfs/mnt/adlsdl/raw/new_directory/vectorstore_batch_107000_108000.faiss
/dbfs/mnt/adlsdl/raw/new_directory/vectorstore_batch_108000_109000.faiss
/dbfs/mnt/adlsdl/raw/new_directory/vectorstore_batch_109000_110000.faiss
/dbfs/mnt/adlsdl/raw/new_directory/vectorstore_batch_110000_111000.faiss
/dbfs/mnt/adlsdl/raw/new_directory/vectorstore_batch_1100